In [1920]:
import pandas as pd
import math as Math
import datetime
from datetime import date,datetime,timedelta
from collections import defaultdict




In [1921]:
projects = pd.read_csv("data/projects.csv")
projects.head()

name location   latitude  longitude  \
0  Uttar Khaishayir Government Primary School  Daudpur  23.619320  90.503657   
1           Uttar Khaishayir General Hospital  Daudpur  23.619320  90.503657   
2     Fazlul Rahman Memorial General Hospital   Tarabo  23.714408  90.517119   
3           Noapara Government Primary School   Tarabo  23.729359  90.508910   
4                    Noapara General Hospital   Tarabo  23.729359  90.508910   

    exec  cost  timespan project_id  \
0  MOEDU     4         3   proj9280   
1    LGD    15         5   proj9681   
2    LGD    25         5   proj3281   
3  MOEDU     3         3   proj4207   
4    LGD    15         5   proj9465   

                                                goal  start_date  completion  \
0  Extending education facilities to the neighbor...  2023-01-02        0.00   
1  Extending healthcare facilities to the neighbo...  2022-12-26        0.00   
2  Extending healthcare facilities to the neighbo...  2022-03-10       15.62   
3  Extending education facilities to the neighbor...  2023-01-17        0.00   
4  Extending healthcare facilities to the neighbo...  2021-11-04       22.52   

   actual_cost  
0         0.00  
1         0.00  
2         3.90  
3         0.00  
4         3.38

In [1922]:
proposals = pd.read_csv("data/proposals.csv")
proposals.head()

name location   latitude  \
0                   Uttar Khaishayir Community Park  Daudpur  23.619320   
1  Fazlul Rahman Memorial Government Primary School   Tarabo  23.714408   
2             Fazlul Rahman Memorial Community Park   Tarabo  23.714408   
3            No. 79 Barpa Government Primary School   Tarabo  23.746950   
4                       No. 79 Barpa Community Park   Tarabo  23.746950   

   longitude   exec  cost  timespan project_id  \
0  90.503657    LGD     2         1   prop3072   
1  90.517119  MOEDU     3         3   prop7106   
2  90.517119    LGD     1         1   prop5730   
3  90.541728  MOEDU     4         3   prop7655   
4  90.541728    LGD     2         1   prop2195   

                                                goal proposal_date  
0  Extending recreational facilities to the neigh...    2022-12-20  
1  Extending education facilities to the neighbor...    2022-12-20  
2  Extending recreational facilities to the neigh...    2022-12-20  
3  Extending education facilities to the neighbor...    2022-12-20  
4  Extending recreational facilities to the neigh...    2022-12-20

In [1923]:
constraints = pd.read_csv("data/constraints.csv")
constraints.head()

code  max_limit         constraint_type
0    MOEDU         25  executing_agency_limit
1      LGD         75  executing_agency_limit
2  Daudpur          8          location_limit
3  Kanchan          5          location_limit
4    Pabna          1          location_limit

In [1924]:
components = pd.read_csv("data/components.csv")
components.head()

project_id ececuting_agency component_id component_type depends_on  \
0   proj9280            MOEDU     comp1459          goods        NaN   
1   proj9280            MOEDU     comp3869          works        NaN   
2   proj9681              LGD     comp4745          goods        NaN   
3   proj9681              LGD     comp3027          works        NaN   
4   proj3281              LGD     comp2119          goods        NaN   

   budget ratio  
0          0.40  
1          0.60  
2          0.30  
3          0.70  
4          0.45

In [1925]:
def string_to_date(str):
    str = str.split("-")
    return date(int(str[0]), int(str[1]), int(str[2]))

def find_project(id):
    for i in range(proposals.shape[0]):
        if id == proposals["project_id"][i]:
            return proposals[i]
        
    return "Proposal Not Found!"

def find_proposal(id):
    for i in range(projects.shape[0]):
        if id == projects["project_id"][i]:
            return projects[i]
        
    return "Project Not Found!"


In [1926]:
days = defaultdict(lambda : {
    "locations": [],
    "agency": [],
    "cost": [], 
})

component = defaultdict(lambda :{
    "day": [],
    "status": False
})
                        
constraint = defaultdict(lambda : {
    "loclimit": Math.inf,
    "costlimit": Math.inf,
    "countlimit": Math.inf,
    "dependency": []
})

component_queue = []


yearCost = defaultdict(lambda : {
    "LGED": 0,
    "RDA": 0,
    "BREB": 0,
    "BWDB": 0,
    "BPDB": 0,
    "BTRC": 0,
    "BBA": 0,
    "PWD": 0,
    "LGD": 0,
    "MOEDU": 0,
    "ECNEC": 0,
    "MOP": 0
})

projectComponent = defaultdict(lambda : {
    "comp": []
})

#print(constraint["10"])

In [1927]:
def already_expense(row):
    tday = date.today() - string_to_date(row['start_date'])
    cday = date.today() - date(2022, 1, 1)
    if tday < cday:
        tday = cday
    cost = (row["completion"] / 100.0) * row["cost"] * (cday / tday)
    
    yearCost[2022][row["exec"]] = yearCost[2022][row["exec"]] + cost


def project_proposal():
    conv = list()
    for idx, row in projects.iterrows():
        if string_to_date(row['start_date']) < date.today():
            already_expense(row)
            completion = 1 - row["completion"] / 100
            row["cost"] = row["cost"] * completion
            row["timespan"] = row["timespan"] * completion
            row["start_date"] = "2022-12-20"
        conv.append(row)
        
    return conv

converted_projects = project_proposal()        

In [1928]:
#constraints.head()
def setConstraint():
    for i in range(constraints.shape[0]):
        if constraints["constraint_type"][i] == "executing_agency_limit":
            constraint[constraints["code"][i]]["countlimit"] = constraints["max_limit"][i]
        elif constraints["constraint_type"][i] == "yearly_funding":
            constraint[constraints["code"][i]]["costlimit"] = constraints["max_limit"][i]
        elif constraints["constraint_type"][i] == "location_limit":
            constraint[constraints["code"][i]]["loclimit"] = constraints["max_limit"][i]
    
    #dependency
    for i in range(components.shape[0]):
        projectComponent[components["project_id"][i]]["comp"].append((components["component_id"][i], components["budget ratio"][i]))
        if not pd.isna(components["depends_on"][i]):
            constraint[components["component_id"][i]]["dependency"].append(components["depends_on"][i])        

setConstraint()
#print(projectComponent)
    

In [1929]:
def projectDivideIntoComponent(row):
    tm, cs, idx, aj = row["timespan"] * 365, row["cost"], row["project_id"], row["exec"]
    if tm == 0.0:
        return 0
    for k in range(len(projectComponent[idx]["comp"])):
        component_queue.append([int(tm), (cs * projectComponent[idx]["comp"][k][1]) / tm, projectComponent[idx]["comp"][k][0], aj])
    
    return int(tm)
    
def projectAssign():
    #tm = 0
    #for row in converted_projects: #kemne row select korbe?
        #tm = tm + projectDivideIntoComponent(row)
    #print(tm)
    for idx, row in projects.iterrows():
        projectDivideIntoComponent(row)
    
        
def agencyCapability(day, aj):
    lm = constraint[aj]["countlimit"]
    cnt = len([a for a in days[day]["agency"] if a==aj]) 
    return cnt < lm

def yearlyBudgetBound(day, aj, costPerDay):
    lm = constraint[aj]["costlimit"]
    yr = datetime.strptime(day, "%Y-%m-%d").year
    cst = yearCost[yr][aj] + costPerDay
    return cst <= lm

def componentLocation(cid):
    proID = components.loc[components['component_id'] == cid].iloc[0]['project_id']
    loc = projects.loc[projects['project_id'] == proID].iloc[0]['location']
    return loc

def locationBound(day, loc):
    lm = constraint[loc]["loclimit"]
    apd = len([a for a in days[day]["locations"] if a==loc]) 
    return apd < lm

def dependencyBound(cid):
    if len(constraint[cid]["dependency"]) == 0:
        return True
    return len([a for a in constraint[cid]["dependency"] if component[a]["status"] == False]) <= 0

def nextxthDay(day, x):
    return (day + timedelta(days=x)).strftime('%Y-%m-%d')
        
projectAssign()
#constraint

In [1930]:
def handleEventRRQone(day, event):
    #print(day)
    event = list(event)
    tr, cs, cid, aj = int(event[0]), event[1], event[2], event[3]
    loc = componentLocation(event[2])
    flag = agencyCapability(day, aj) and locationBound(day, loc) and yearlyBudgetBound(day, aj, cs) and dependencyBound(cid)
    
    if flag:
        component[cid]["day"].append(day)
        days[day]["locations"].append(loc)
        days[day]["agency"].append(aj)
        yr = datetime.strptime(day, "%Y-%m-%d").year
        yearCost[yr][aj] = yearCost[yr][aj] + cs
        #print(yearCost[yr][aj])
        event[0] = tr - 1
        #print(event[0], tr)
        if event[0] > 0:
            component_queue.append(event)
        else:
            component[event[2]]["status"] = True
        
    return flag 

def RRplusSJF(): 
    cq = sorted(component_queue)
    vis = [False] * len(cq)
    for i in range(1000000):
        for j in range(len(cq)):
            if vis[j]:
                continue
            day = (date.today() + timedelta(days=i)).strftime('%Y-%m-%d')
            event = list(cq[j])
            tr, cs, cid, aj = int(event[0]), event[1], event[2], event[3]
            loc = componentLocation(event[2])
            flag = agencyCapability(day, aj) and locationBound(day, loc) and yearlyBudgetBound(day, aj, cs) and dependencyBound(cid)

            if flag:
                component[cid]["day"].append(day)
                days[day]["locations"].append(loc)
                days[day]["agency"].append(aj)
                yr = datetime.strptime(day, "%Y-%m-%d").year
                yearCost[yr][aj] = yearCost[yr][aj] + cs
                event[0] = tr - 1
                if event[0] > 0:
                    cq[j] = event
                else:
                    vis[j] = True
                    component[event[2]]["status"] = True
        if len([a for a in vis if a == False]) == 0:
            break
        
RRplusSJF()

In [1931]:
def handleEventSJF(day, event):
    event = list(event)
    tr, cs, cid, aj = event[0], event[1], event[2], event[3]
    loc = componentLocation(event[2])
    flag = agencyCapability(day, aj) and locationBound(day, loc) and yearlyBudgetBound(day, aj, cs) and dependencyBound(cid)
    
    if flag:
        component[event[2]]["day"].append(day)
        days[day]["locations"].append(loc)
        days[day]["agency"].append(aj)
        yr = datetime.strptime(day, "%Y-%m-%d").year
        #print(yr)
        yearCost[yr][aj] = yearCost[yr][aj] + cs
        event[0] = event[0] - 1
        if event[0] > 0:
            handleEventSJF(nextxthDay(datetime.strptime(day, "%Y-%m-%d"), 1), event)
        else:
            component[event[2]]["status"] = True
        
    return flag 

def SJF():
    dd = 0
    cq = sorted(component_queue)
    while len(cq) != 0:
        check = False
        for i in range(len(cq)):  
            if handleEventSJF((date.today() + timedelta(days=dd)).strftime('%Y-%m-%d'), cq[i]):
                del cq[i]
                check = True
                break
        if not check:
            dd = dd + 1
        
#SJF()            
component

defaultdict(<function __main__.<lambda>()>,
            {'comp122': {'day': ['2022-12-21',
               '2022-12-22',
               '2022-12-23',
               '2022-12-24',
               '2022-12-25',
               '2022-12-26',
               '2022-12-27',
               '2022-12-28',
               '2022-12-29',
               '2022-12-30',
               '2022-12-31',
               '2023-01-01',
               '2023-01-02',
               '2023-01-03',
               '2023-01-04',
               '2023-01-05',
               '2023-01-06',
               '2023-01-07',
               '2023-01-08',
               '2023-01-09',
               '2023-01-10',
               '2023-01-11',
               '2023-01-12',
               '2023-01-13',
               '2023-01-14',
               '2023-01-15',
               '2023-01-16',
               '2023-01-17',
               '2023-01-18',
               '2023-01-19',
               '2023-01-20',
               '2023-01-21',
          

In [1932]:


def mindate(d1, d2):
    return d1 if (d1-d2).seconds>0 else d2

def maxdate(d1, d2):
    return d1 if (d1-d2).seconds>0 else d2


def output():
    project_dict = defaultdict(lambda :{
        "start": date(2099, 1, 1),
        "end": date(1900, 1, 1)
    })
    
    for k,v in component.items():
        project_id = components[components['component_id'] == k].iloc[0]['project_id']
        project_dict[project_id]['start'] = mindate(project_dict[project_id]['start'], datetime.strptime(v['day'][0], '%Y-%m-%d').date())
        project_dict[project_id]['end'] = maxdate(project_dict[project_id]['end'],datetime.strptime(v['day'][-1], '%Y-%m-%d').date())
    
    return project_dict

output()
    

defaultdict(<function __main__.output.<locals>.<lambda>()>,
            {'proj1206': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj5580': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj3120': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj9145': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj7969': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj1092': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj5879': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj8160': {'start': datetime.date(2022, 12, 21),
              'end': datetime.date(2023, 12, 20)},
             'proj99